# Array dynamics

In [1]:
#Locale settings
import locale
# Set to German locale to get comma decimal separater
locale.setlocale(locale.LC_NUMERIC, "deu_DEU")
import numpy as np
import matplotlib.pyplot as plt
plt.rcdefaults()
# Tell matplotlib to use the locale we set above
plt.rcParams['axes.formatter.use_locale'] = True

In [2]:
%matplotlib qt
from qsweepy import *
from qsweepy.ponyfiles import *
from qsweepy.instruments import *
from qsweepy.save_pkl import save_pkl
import matplotlib.pyplot as plt
import numpy as np
from matplotlib import interactive
interactive(True)
from importlib import reload

sample_name = '1910-0802-array'
from qsweepy.ponyfiles.data_structures import *

Failed loading module Keysight_M3102A:  No module named 'keysightSD1'
Failed loading module Keysight_M3202A:  No module named 'keysightSD1'


In [3]:
from qsweepy.tunable_coupling_transmons.Misis_array_qubit_February_2020_setup \
import device_settings, pulsed_settings, hardware_setup
hardware = hardware_setup(device_settings, pulsed_settings)
hardware.open_devices()


Discovered device `dev8108`: HDAWG8 with options MF.
Creating an API session for device `dev8108` on `127.0.0.1`, `8004` with apilevel `6`.
Trigger output is assigned to AWG Trigger 1, controlled by AWG sequencer commands.
Trigger output is assigned to AWG Trigger 2, controlled by AWG sequencer commands.
Trigger output is assigned to AWG Trigger 3, controlled by AWG sequencer commands.
Trigger output is assigned to AWG Trigger 4, controlled by AWG sequencer commands.
Output is assigned to Output 1 Marker 1.
Output is assigned to Output 1 Marker 2.
Output is assigned to Output 2 Marker 1.
Output is assigned to Output 2 Marker 2.
Sequencer #0: Compilation successful with no warnings, will upload the program to the instrument.
Sequencer #0: 1 awgModule/progress: 1.00
Sequencer #0: Upload to the instrument successful.
Time:  0.7092011999999999
Sequencer #1: Compilation successful with no warnings, will upload the program to the instrument.
Sequencer #1: 5 awgModule/progress: 1.00
Sequencer

D:\qtlab_replacement\qsweepy\config.py:65: YAMLLoadWarning:

calling yaml.load() without Loader=... is deprecated, as the default Loader is unsafe. Please read https://msg.pyyaml.org/load for full details.



In [12]:

reload(exdir_db)
reload(database)
reload(sweep_extras)
import imp
from qsweepy.qubit_calibrations import readout_passthrough, readout_pulse
from qsweepy.fitters import exp_sin, fit_dataset
from qsweepy import readout_classifier
from qsweepy.qubit_calibrations import gauss_hd
from qsweepy import tomography
from qsweepy import pulses
reload(awg_digital)
reload(awg_iq_multi)
reload(data_reduce)
reload(fitting)
reload(plotting)
reload(tomography)
reload(sweep)
reload(pulses)
reload(awg_channel)
reload(awg_iq_multi)
reload(modem_readout)
reload(qubit_device)
reload(single_shot_readout)
reload(readout_passthrough)
reload(readout_pulse)
reload(exp_sin)
reload(fit_dataset)
reload(exdir_db)
reload(database)
reload(sweep_extras)
reload(readout_classifier)

db = database.MyDatabase()
sweeper = sweep_extras.Sweeper(db, sample_name=sample_name)
exdir_db_inst = exdir_db.Exdir_db(db=db, sample_name=sample_name)

hardware.mcfq.set_exdir_db(exdir_db_inst)
#fq=5.808e9
fq = 4.1e9
fq1=4.393e9
#fq2=6.4505e9
hardware.mcfq.set_all_frequencies(fq)
#hardware.controls['fq1'].set_offset(fq1)
hardware.set_pulsed_mode()
hardware.setup_iq_channel_connections(exdir_db_inst)
device = qubit_device.qubit_device(exdir_db_inst, sweeper, controls = hardware.controls)
device.hardware = hardware
for qubit_id in device.get_qubit_list():
    if qubit_id != '1':
        if np.abs(device.get_qubit_fq(qubit_id=qubit_id) - fq) > 1e6:
            device.set_qubit_fq(qubit_id=qubit_id, fq=fq)
device.set_qubit_fq(qubit_id='1', fq=fq1)
#device.set_qubit_fq(qubit_id='1', fq=fq1)
device.create_pulsed_interfaces(hardware.iq_devices, hardware.fast_controls,
                                extra_channels = {'ro_trg':hardware.ro_trg})

device.setup_modem_readout(hardware)

Sequencer #0: Compilation successful with no warnings, will upload the program to the instrument.
Sequencer #0: 1 awgModule/progress: 1.00
Sequencer #0: Upload to the instrument successful.
Time:  0.6896153000052436
Sequencer #1: Compilation successful with no warnings, will upload the program to the instrument.
Sequencer #1: 1 awgModule/progress: 1.00
Sequencer #1: Upload to the instrument successful.
Time:  0.7468681999962428
Sequencer #2: Compilation successful with no warnings, will upload the program to the instrument.
Sequencer #2: 1 awgModule/progress: 1.00
Sequencer #2: Upload to the instrument successful.
Time:  0.731635299998743
Sequencer #3: Compilation successful with no warnings, will upload the program to the instrument.
Sequencer #3: 2 awgModule/progress: 1.00
Sequencer #3: Upload to the instrument successful.
Time:  0.8295025999977952
Sequencer #0: Compilation successful with no warnings, will upload the program to the instrument.
Sequencer #0: 1 awgModule/progress: 1.0

reference: delay_measurement : 19724
reference: delay_measurement : 19724
reference: delay_measurement : 19724
reference: delay_measurement : 19724
reference: delay_measurement : 19724
reference: delay_measurement : 19724
reference: delay_measurement : 19724
reference: delay_measurement : 19724
reference: delay_measurement : 19724


In [5]:
#exdir_db_inst.select_measurement(measurement_type='Podgon_param').datasets['K'].parameters[1].values
hardware.mcfq.get_qubit_freq_max('1')

5584675076.178481

In [6]:
m = exdir_db_inst.select_measurement(measurement_type='Full_two_tone_fit_Recool',
                                                      metadata={'qubit_id': '1', }).metadata
np.sqrt(8*(float(m['EJ1'])+float(m['EJ2']))*float(m['EC']))

6435015876.816215

# Two-tone spectroscopy (figure out the true frequency of qubit #1)

In [6]:
from qsweepy.qubit_calibrations import spectroscopy
imp.reload(spectroscopy)
result = spectroscopy.measure_fr(device, '1', fr_guess=device.get_qubit_fr('1'))
#device.set_qubit_fq(qubit_id='1', fq=fq1)
spectroscopy.two_tone_spectroscopy(device, '1', device.get_qubit_fq('1'), power_excite=18, span=2e9, 
                                   nop=2001, power_readout=-55, bandwidth=10)

reference: frequency_controls : 19680
fr_guess:  5377230900.748679
load time:  0.04097628593444824
pre_trace_time:  0.000997781753540039
trace 0 time:  0.014993906021118164
trace 1 time:  0.028982877731323242
trace 2 time:  0.04397392272949219
trace 3 time:  0.05796527862548828
Sequencer #0: Compilation successful with no warnings, will upload the program to the instrument.
Sequencer #0: 11 awgModule/progress: 1.00
Sequencer #0: Upload to the instrument successful.
Time:  1.7531606999999667
Sequencer #1: Compilation successful with no warnings, will upload the program to the instrument.
Sequencer #1: 10 awgModule/progress: 1.00
Sequencer #1: Upload to the instrument successful.
Time:  1.5715189999999666
Sequencer #2: Compilation successful with no warnings, will upload the program to the instrument.
Sequencer #2: 11 awgModule/progress: 1.00
Sequencer #2: Upload to the instrument successful.
Time:  1.7482145000000173
Sequencer #3: Compilation successful with no warnings, will upload the

start: 2020-04-15 21:26:20.619370, started/done/total sweeps: 0/2001/2001, 
Measured data: 
'S-parameter': parameters: excitation_frequency (),:[3393000000.0, 5393000000.0] (2001 points) with setter
Frequency (Hz),:[5377230900.75, 5377230900.75] (1 points) without setter
data: [[0.00393615+0.0045917j ]
 [0.00393615+0.0045917j ]
 [0.00393615+0.0045917j ]
 ...
 [0.0013552 +0.00347309j]
 [0.0013552 +0.00347309j]
 [0.00061785+0.00566607j]]

In [7]:
hardware.pna.get_bandwidth()

10.0

In [8]:
import time
sweep_time = hardware.pna.get_sweep_time()
start_time=time.time()
hardware.pna.measure()
print(time.time()-start_time)

0.14591121673583984


In [53]:
m = exdir_db_inst.select_measurement_by_id(19455)
m.datasets['S-parameter'].parameters

Exdir_db.select_measurement_by_id: trying to load measurement state by id:  d:\data\2020-04-12\019455-qubit_frequency-1910-0802-array


[excitation_frequency (),:[5955000000.0, 6955000000.0] (1001 points) with setter,
 Frequency (Hz),:[5380500000.0, 5380500000.0] (1 points) without setter]

In [42]:
device.get_qubit_fq(qubit_id='1')

reference: frequency_controls : 19680


4393000000.0

In [58]:
device.set_qubit_fr(qubit_id='1', fr=result.metadata['fr'])

{'frequency_controls': 15410}


In [17]:
hardware.lo1.get_power()

18.0

# Pulsed measurements for qubit #1

In [14]:
from qsweepy.qubit_calibrations import readout_pulse
imp.reload(readout_passthrough)
for qubit_id in ['1']:
    measurer = readout_passthrough.readout_passthrough(device, qubit_id, 0.4e-6, np.linspace(0.05, 1.0, 12))
measurer

1 32768
first_point:  0 last_point:  48672 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 49600 nop 49600 post_delay 1856 pre_delay 0 pre_delay_reg 0
first_point:  48200 last_point:  48600 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 600 nop 49600 post_delay 1000 pre_delay 48000 pre_delay_reg 6000
first_point:  48200 last_point:  48600 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 600 nop 49600 post_delay 1000 pre_delay 48000 pre_delay_reg 6000
first_point:  48200 last_point:  48600 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 600 nop 49600 post_delay 1000 pre_delay 48000 pre_delay_reg 6000
first_point:  48200 last_point:  48600 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 600 nop 49600 po

start: 2020-04-16 15:09:36.059372, started/done/total sweeps: 0/12/12, 
Measured data: 
'Mean_Voltage_AC': parameters: amplitude (),:[0.05, 1.0] (12 points) with setter
Time (s),:[0.0, 5.11e-07] (512 points) without setter
data: [[  0.39764978 -0.59239457j   0.57227478 +0.84789543j
   -0.63054522 +0.62799543j ...  -2.21272522 -1.10760457j
    1.85614978 +2.30353043j  -3.37875522 -4.11272957j]
 [ -0.16218804 -1.47578828j   0.71637696 +1.45180172j
    0.11343196 -0.21348828j ...  -6.15990804 -4.38046328j
    5.95034196 +6.46565172j  -5.03772304-10.22373828j]
 [ -0.42744902 +0.46904149j  -0.59427402 +1.57378649j
   -0.92545402 +0.16697149j ... -11.54578902 -6.61596351j
    9.79608598+11.21121649j  -9.01916902-17.54349351j]
 ...
 [ -1.70422933 -1.32226526j   0.66903067 -0.31049026j
   -1.37665433 -0.54728526j ... -42.51029933-12.01507526j
   37.53682567+36.98450474j -36.27742933-55.25756526j]
 [ -1.49163405 -1.38318643j  -0.41748405 +0.09732357j
   -2.33978405 -2.23958643j ... -47.50808905

In [26]:
from qsweepy.qubit_calibrations import calibrated_readout
imp.reload(calibrated_readout)
calibrated_readout.readout_fidelity_scan(device, 
                                        '1', 
                                        readout_pulse_lengths=[0.3e-6], 
                                        readout_pulse_amplitudes=np.linspace(0.1, 0.65, 19),
                                        ignore_other_qubits=True)

1 32768
reference: channel_amplitudes : 15679
reference: gauss_hd_Rabi_amplitude_adaptive : 15701
Exdir_db.select_measurement_by_id: trying to load measurement state by id:  d:\data\2020-04-02\015679-channel_amplitudes-1910-0802-array
first_point:  48296 last_point:  48600 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 600 nop 49600 post_delay 1000 pre_delay 48000 pre_delay_reg 6000
first_point:  48296 last_point:  48600 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 600 nop 49600 post_delay 1000 pre_delay 48000 pre_delay_reg 6000
first_point:  48184 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 200 nop 49600 post_delay 1320 pre_delay 48080 pre_delay_reg 6010


C:\ProgramData\Anaconda3\lib\site-packages\sklearn\model_selection\_split.py:1978: FutureWarning:

The default value of cv will change from 3 to 5 in version 0.22. Specify it explicitly to silence this warning.



D:\qtlab_replacement\qsweepy\instrument_drivers\HDAWG_1808_new.py:607: ComplexWarning:

Casting complex values to real discards the imaginary part



first_point:  48296 last_point:  48600 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 600 nop 49600 post_delay 1000 pre_delay 48000 pre_delay_reg 6000
first_point:  48296 last_point:  48600 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 600 nop 49600 post_delay 1000 pre_delay 48000 pre_delay_reg 6000
first_point:  48184 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 200 nop 49600 post_delay 1320 pre_delay 48080 pre_delay_reg 6010


C:\ProgramData\Anaconda3\lib\site-packages\sklearn\model_selection\_split.py:1978: FutureWarning:

The default value of cv will change from 3 to 5 in version 0.22. Specify it explicitly to silence this warning.



...

C:\ProgramData\Anaconda3\lib\site-packages\sklearn\model_selection\_split.py:1978: FutureWarning:

The default value of cv will change from 3 to 5 in version 0.22. Specify it explicitly to silence this warning.



load time:  0.46860814094543457
pre_trace_time:  0.0004990100860595703
trace 0 time:  0.03643155097961426
trace 1 time:  0.06886982917785645
trace 2 time:  0.10030984878540039
trace 3 time:  0.13324713706970215
trace 4 time:  0.16568565368652344


C:\ProgramData\Anaconda3\lib\site-packages\numpy\core\memmap.py:331: FutureWarning:

Using a non-tuple sequence for multidimensional indexing is deprecated; use `arr[tuple(seq)]` instead of `arr[seq]`. In the future this will be interpreted as an array index, `arr[np.array(seq)]`, which will result either in an error or a different result.



trace 5 time:  0.19912123680114746
trace 6 time:  0.23106098175048828
trace 7 time:  0.26399850845336914
trace 8 time:  0.2984321117401123
trace 9 time:  0.33336663246154785
trace 10 time:  0.3732905387878418
trace 11 time:  0.40672731399536133
trace 12 time:  0.439164400100708
trace 13 time:  0.4716036319732666
trace 14 time:  0.5040421485900879
trace 15 time:  0.5240039825439453
trace 16 time:  0.5649261474609375
trace 17 time:  0.5973646640777588
trace 18 time:  0.6178240776062012


start: 2020-04-06 13:53:41.326025, started/done/total sweeps: 0/19/19, 
Measured data: 
'fidelity': parameters: length (s),:[3e-07, 3e-07] (1 points) with setter
amplitude (),:[0.1, 0.65] (19 points) with setter
data: [[0.50553333 0.50461667 0.51381667 0.52311667 0.5331     0.53095
  0.54516667 0.55258333 0.55365    0.5606     0.5812     0.58271667
  0.59558333 0.60038333 0.60796667 0.61156667 0.61241667 0.61536667
  0.62083333]]
'confusion_matrix': parameters: length (s),:[3e-07, 3e-07] (1 points) with setter
amplitude (),:[0.1, 0.65] (19 points) with setter
Target state (),:[0, 1] (2 points) without setter
Classified state (),:[0, 1] (2 points) without setter
data: [[[[0.5794     0.4206    ]
   [0.4749     0.5251    ]]

  [[0.57593333 0.42406667]
   [0.46533333 0.53466667]]

  [[0.5641     0.4359    ]
   [0.44496667 0.55503333]]

  [[0.55063333 0.44936667]
   [0.42063333 0.57936667]]

  [[0.57813333 0.42186667]
   [0.4323     0.5677    ]]

  [[0.5934     0.4066    ]
   [0.45033333 0.

In [5]:
from qsweepy.qubit_calibrations import readout_pulse
readout_pulse.get_calibrated_measurer(device, ['1'])

reference: frequency_controls : 13617
reference: channel_calibration : 13898
reference: fidelity_scan : 15065
reference: ('readout_pulse', '1') : 15066
reference: readout_pulse : 15067
reference: delay_calibration : 14711


(start: 2020-03-26 16:46:38.782000, started/done/total sweeps: 0/0/0, 
 Measured data: ,
 <qsweepy.instrument_drivers.TSW14J56driver.TSW14J56_evm_reducer at 0x22a5fbcc128>)

In [47]:
imp.reload(readout_pulse)

<module 'qsweepy.qubit_calibrations.readout_pulse' from 'D:\\qtlab_replacement\\qsweepy\\qubit_calibrations\\readout_pulse.py'>

In [11]:
device.get_qubit_fq('1')

reference: frequency_controls : 19509


6451000000.0

In [15]:
from qsweepy.qubit_calibrations import Rabi, Ramsey
from qsweepy.qubit_calibrations import channel_amplitudes
for qubit_id in ['1']:#device.get_qubit_list():
    #readout_pulse.get_readout_calibration(device, 
    #                        readout_pulse.get_qubit_readout_pulse(device, qubit_id), 
    #                        excitation_pulse=None, recalibrate=True)
    channel = channel_amplitudes.channel_amplitudes(device, **{'iq_ex1_q'+qubit_id:1.0})
    #Ramsey.get_Ramsey_coherence_measurement(device, '1')
    #Rabi.Rabi_rect_adaptive(device, qubit_id, channel_amplitudes=channel)
    Rabi.Rabi_rect(device, qubit_id, channel_amplitudes=channel, lengths=np.linspace(0, 1000e-9, 101))

Requested:  metadata: {'iq_ex1_q1': '1.0'} references: {('channel_calibration', 'iq_ex1_q1'): 19763}
reference: ('channel_calibration', 'iq_ex1_q1') : 19763
Obtained:  metadata: {'iq_ex1_q1': '1.0'} references: {'channel_calibration': 19763}
invoking get_qubit_readout_pulse on line 58
reference: frequency_controls : 19680
reference: channel_calibration : 19691
reference: frequency_controls : 19680
reference: channel_calibration : 19691
Failed to get readout pulse from fidelity scan, fall back to passthrough
reference: frequency_controls : 19680
reference: channel_calibration : 19691


Traceback (most recent call last):
  File "D:\qtlab_replacement\qsweepy\qubit_calibrations\readout_pulse.py", line 101, in get_qubit_readout_pulse
    measurement = device.exdir_db.select_measurement(measurement_type='readout_fidelity_scan', metadata=metadata_fidelity_scan, references_that=references)
  File "D:\qtlab_replacement\qsweepy\ponyfiles\exdir_db.py", line 112, in select_measurement
    filename_db = list(measurement_db_list.order_by(lambda d: desc(d.id)).limit(1))[0].filename
IndexError: list index out of range
Traceback (most recent call last):
  File "D:\qtlab_replacement\qsweepy\qubit_calibrations\readout_pulse.py", line 191, in get_uncalibrated_measurer
    qubit_readout_pulse_, measurer = get_calibrated_measurer(device, [qubit_id], recalibrate=False)
  File "D:\qtlab_replacement\qsweepy\qubit_calibrations\calibrated_readout.py", line 58, in get_calibrated_measurer
    qubit_readout_pulse = get_multi_qubit_readout_pulse(device, qubit_ids, recalibrate=recalibrate)
  File 

reference: passthrough_measurement : 19783
reference: readout_pulse : 19784
reference: modem_calibration : 19726
1 32768
initial_axes_order [(2, 0)]
first_point:  0 last_point:  48776 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 49600 nop 49600 post_delay 1648 pre_delay 0 pre_delay_reg 0
first_point:  48200 last_point:  48600 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 600 nop 49600 post_delay 1000 pre_delay 48000 pre_delay_reg 6000
first_point:  48296 last_point:  48600 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 600 nop 49600 post_delay 1000 pre_delay 48000 pre_delay_reg 6000
first_point:  48264 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 200 nop 49600 post_delay 1320 pre_delay 48080 pre_delay_reg 6010
first_point:  48256 

first_point:  47904 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 600 nop 49600 post_delay 1320 pre_delay 47680 pre_delay_reg 5960
first_point:  47896 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 600 nop 49600 post_delay 1320 pre_delay 47680 pre_delay_reg 5960
first_point:  47888 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 600 nop 49600 post_delay 1320 pre_delay 47680 pre_delay_reg 5960
first_point:  47880 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 600 nop 49600 post_delay 1320 pre_delay 47680 pre_delay_reg 5960
first_point:  47864 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 600 nop 49600 p

first_point:  47520 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 2000 nop 49600 post_delay 1320 pre_delay 46280 pre_delay_reg 5785
first_point:  47504 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 2000 nop 49600 post_delay 1320 pre_delay 46280 pre_delay_reg 5785
first_point:  47496 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 2000 nop 49600 post_delay 1320 pre_delay 46280 pre_delay_reg 5785
first_point:  47488 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 2000 nop 49600 post_delay 1320 pre_delay 46280 pre_delay_reg 5785
first_point:  47480 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 2000 nop 49

In [28]:
plt.plot(hardware.hdawg._waveforms[7])

In [32]:
from qsweepy.qubit_calibrations import calibrated_readout, readout_pulse
readout_pulse.get_qubit_readout_pulse

<function qsweepy.qubit_calibrations.readout_pulse.get_qubit_readout_pulse(device, qubit_id, length=None)>

In [5]:
from qsweepy.qubit_calibrations import calibrated_readout, readout_pulse
#
#calibrated_readout.calibrate_readout(device, '1', readout_pulse.get_qubit_readout_pulse(device, '1'))
qubit_readout_pulse, readout_device = calibrated_readout.get_calibrated_measurer(device, ['1'], force_recalibration=True)
#calibrated_readout.get_calibrated_measurer(device, ['1'], force_recalibration=True)
calibrated_readout.calibrate_preparation_and_readout_confusion(device, qubit_readout_pulse, readout_device)

reference: frequency_controls : 15410
reference: channel_calibration : 15490
reference: fidelity_scan : 15714
reference: ('readout_pulse', '1') : 15715
None
1 32768


Traceback (most recent call last):
  File "D:\qtlab_replacement\qsweepy\qubit_calibrations\calibrated_readout.py", line 68, in get_calibrated_measurer
    raise ValueError('Forcing recalibration')
ValueError: Forcing recalibration


reference: channel_amplitudes : 15679
reference: gauss_hd_Rabi_amplitude_adaptive : 15701
Exdir_db.select_measurement_by_id: trying to load measurement state by id:  d:\data\2020-04-02\015679-channel_amplitudes-1910-0802-array
first_point:  0 last_point:  48776 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 49600 nop 49600 post_delay 1648 pre_delay 0 pre_delay_reg 0
first_point:  48296 last_point:  48600 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 600 nop 49600 post_delay 1000 pre_delay 48000 pre_delay_reg 6000
first_point:  48296 last_point:  48600 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 600 nop 49600 post_delay 1000 pre_delay 48000 pre_delay_reg 6000
first_point:  48184 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 200 nop

C:\ProgramData\Anaconda3\lib\site-packages\sklearn\model_selection\_split.py:1978: FutureWarning:

The default value of cv will change from 3 to 5 in version 0.22. Specify it explicitly to silence this warning.



load time:  0.25551533699035645
pre_trace_time:  0.0009968280792236328
trace 0 time:  0.017467021942138672
trace 1 time:  0.031440019607543945
trace 2 time:  0.04441523551940918
trace 3 time:  0.05838918685913086
trace 4 time:  0.07236242294311523
trace 5 time:  0.08583712577819824
trace 6 time:  0.09981060028076172
trace 7 time:  0.11478161811828613
trace 8 time:  0.1287550926208496
trace 9 time:  0.14322757720947266
trace 10 time:  0.15720081329345703
trace 11 time:  0.17167377471923828
trace 12 time:  0.19912171363830566


C:\ProgramData\Anaconda3\lib\site-packages\numpy\core\memmap.py:331: FutureWarning:

Using a non-tuple sequence for multidimensional indexing is deprecated; use `arr[tuple(seq)]` instead of `arr[seq]`. In the future this will be interpreted as an array index, `arr[np.array(seq)]`, which will result either in an error or a different result.



trace 13 time:  0.21958565711975098
reference: channel_amplitudes : 15679
reference: gauss_hd_Rabi_amplitude_adaptive : 15701
Exdir_db.select_measurement_by_id: trying to load measurement state by id:  d:\data\2020-04-02\015679-channel_amplitudes-1910-0802-array


D:\qtlab_replacement\qsweepy\instrument_drivers\HDAWG_1808_new.py:607: ComplexWarning:

Casting complex values to real discards the imaginary part



first_point:  48184 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 200 nop 49600 post_delay 1320 pre_delay 48080 pre_delay_reg 6010
load time:  0.050405263900756836
pre_trace_time:  0.001995563507080078
trace 0 time:  0.029443740844726562


start: 2020-04-05 11:14:41.616117, started/done/total sweeps: 0/2/2, 
Measured data: 
'resultnumbers': parameters: Target state (),:[0, 1] (2 points) with setter
State (),:[0, 1] (2 points) without setter
data: [[25476. 24524.]
 [18033. 31967.]]

In [22]:
m[0].references

{'readout_pulse': 15066}

In [17]:
from qsweepy.qubit_calibrations import excitation_pulse
from qsweepy.qubit_calibrations import relaxation
#excitation_pulse.get_rect_excitation_pulse(device, '1', np.pi)
relaxation.relaxation_adaptive(device, '1', expected_T1=2e-6)

reference: frequency_controls : 15410
reference: channel_calibration : 15490
reference: fidelity_scan : 15561
reference: ('readout_pulse', '1') : 15562
reference: readout_pulse : 15563
reference: delay_calibration : 15517
reference: frequency_controls : 15410
good Rabi fits: [15581]
trying  15581
Exdir_db.select_measurement_by_id: trying to load measurement state by id:  d:\data\2020-04-01\015581-fit_dataset_1d-1910-0802-array
Exdir_db.select_measurement_by_id: trying to load measurement state by id:  d:\data\2020-04-01\015580-Rabi_rect-1910-0802-array
reference: channel_amplitudes : 15577
reference: Rabi_rect : 15580
Exdir_db.select_measurement_by_id: trying to load measurement state by id:  d:\data\2020-04-01\015577-channel_amplitudes-1910-0802-array
initial_axes_order [(2, 0)]


Traceback (most recent call last):
  File "D:\qtlab_replacement\qsweepy\qubit_calibrations\excitation_pulse.py", line 124, in __init__
    measurement = self.device.exdir_db.select_measurement(measurement_type='qubit_excitation_pulse', metadata=metadata, references_that=references)
  File "D:\qtlab_replacement\qsweepy\ponyfiles\exdir_db.py", line 112, in select_measurement
    filename_db = list(measurement_db_list.order_by(lambda d: desc(d.id)).limit(1))[0].filename
IndexError: list index out of range
C:\ProgramData\Anaconda3\lib\site-packages\numpy\core\fromnumeric.py:3118: RuntimeWarning:

Mean of empty slice.

C:\ProgramData\Anaconda3\lib\site-packages\numpy\core\_methods.py:85: RuntimeWarning:

invalid value encountered in double_scalars



first_point:  48224 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 200 nop 49600 post_delay 1320 pre_delay 48080 pre_delay_reg 6010


D:\qtlab_replacement\qsweepy\fitters\exp.py:21: RuntimeWarning:

invalid value encountered in true_divide

D:\qtlab_replacement\qsweepy\fitters\exp.py:21: RuntimeWarning:

divide by zero encountered in true_divide



first_point:  48176 last_point:  48232 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 200 nop 49600 post_delay 1368 pre_delay 48032 pre_delay_reg 6004
first_point:  48128 last_point:  48184 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 200 nop 49600 post_delay 1416 pre_delay 47984 pre_delay_reg 5998
first_point:  48072 last_point:  48128 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 200 nop 49600 post_delay 1472 pre_delay 47928 pre_delay_reg 5991
first_point:  48024 last_point:  48080 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 200 nop 49600 post_delay 1520 pre_delay 47880 pre_delay_reg 5985
first_point:  47976 last_point:  48032 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 200 nop 49600 p

first_point:  44224 last_point:  44280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 200 nop 49600 post_delay 5320 pre_delay 44080 pre_delay_reg 5510
Waiting to join deferred threads:
load time:  0.038926124572753906
pre_trace_time:  0.0004987716674804688
trace 0 time:  0.013973236083984375
load time:  0.038427114486694336
pre_trace_time:  0.000997781753540039
trace 0 time:  0.012975454330444336


KeyError: 'decay_goodness_test'

In [14]:
from qsweepy.qubit_calibrations import Ramsey
Ramsey.Ramsey_adaptive(device, '1', expected_T2=1e-6)

reference: frequency_controls : 19509
invoking get_qubit_readout_pulse on line 58
reference: frequency_controls : 19509
reference: channel_calibration : 19516
invoking get_qubit_readout_pulse on line 196


Traceback (most recent call last):
  File "D:\qtlab_replacement\qsweepy\qubit_calibrations\readout_pulse.py", line 101, in get_qubit_readout_pulse
    measurement = device.exdir_db.select_measurement(measurement_type='readout_fidelity_scan', metadata=metadata_fidelity_scan, references_that=references)
  File "D:\qtlab_replacement\qsweepy\ponyfiles\exdir_db.py", line 112, in select_measurement
    filename_db = list(measurement_db_list.order_by(lambda d: desc(d.id)).limit(1))[0].filename
IndexError: list index out of range
Traceback (most recent call last):
  File "D:\qtlab_replacement\qsweepy\qubit_calibrations\readout_pulse.py", line 189, in get_uncalibrated_measurer
    qubit_readout_pulse_, measurer = get_calibrated_measurer(device, [qubit_id], recalibrate=False)
  File "D:\qtlab_replacement\qsweepy\qubit_calibrations\calibrated_readout.py", line 58, in get_calibrated_measurer
    qubit_readout_pulse = get_multi_qubit_readout_pulse(device, qubit_ids, recalibrate=recalibrate)
  File 

reference: frequency_controls : 19509
reference: channel_calibration : 19516
1 32768
reference: frequency_controls : 19509
good Rabi fits: []
Requested:  metadata: {'iq_ex1_q1': '1.0'} references: {('channel_calibration', 'iq_ex1_q1'): 19466}
reference: ('channel_calibration', 'iq_ex1_q1') : 19466
Obtained:  metadata: {'iq_ex1_q1': '1.0'} references: {'channel_calibration': 19466}
reference: frequency_controls : 19509
good Rabi fits: []
0 8e-08 1e-09
invoking get_qubit_readout_pulse on line 58
reference: frequency_controls : 19509
reference: channel_calibration : 19516
invoking get_qubit_readout_pulse on line 196


Traceback (most recent call last):
  File "D:\qtlab_replacement\qsweepy\qubit_calibrations\readout_pulse.py", line 101, in get_qubit_readout_pulse
    measurement = device.exdir_db.select_measurement(measurement_type='readout_fidelity_scan', metadata=metadata_fidelity_scan, references_that=references)
  File "D:\qtlab_replacement\qsweepy\ponyfiles\exdir_db.py", line 112, in select_measurement
    filename_db = list(measurement_db_list.order_by(lambda d: desc(d.id)).limit(1))[0].filename
IndexError: list index out of range

During handling of the above exception, another exception occurred:

Traceback (most recent call last):
  File "D:\qtlab_replacement\qsweepy\qubit_calibrations\readout_pulse.py", line 101, in get_qubit_readout_pulse
    measurement = device.exdir_db.select_measurement(measurement_type='readout_fidelity_scan', metadata=metadata_fidelity_scan, references_that=references)
  File "D:\qtlab_replacement\qsweepy\ponyfiles\exdir_db.py", line 112, in select_measurement
    fi

reference: frequency_controls : 19509
reference: channel_calibration : 19516
1 32768
reference: frequency_controls : 19509
good Rabi fits: []
Requested:  metadata: {'iq_ex1_q1': '1.0'} references: {('channel_calibration', 'iq_ex1_q1'): 19466}
reference: ('channel_calibration', 'iq_ex1_q1') : 19466
Obtained:  metadata: {'iq_ex1_q1': '1.0'} references: {'channel_calibration': 19466}
reference: frequency_controls : 19509
good Rabi fits: []
0 8e-08 1e-09
invoking get_qubit_readout_pulse on line 58
reference: frequency_controls : 19509
reference: channel_calibration : 19516
invoking get_qubit_readout_pulse on line 196


...

Traceback (most recent call last):
  File "D:\qtlab_replacement\qsweepy\qubit_calibrations\readout_pulse.py", line 101, in get_qubit_readout_pulse
    measurement = device.exdir_db.select_measurement(measurement_type='readout_fidelity_scan', metadata=metadata_fidelity_scan, references_that=references)
  File "D:\qtlab_replacement\qsweepy\ponyfiles\exdir_db.py", line 112, in select_measurement
    filename_db = list(measurement_db_list.order_by(lambda d: desc(d.id)).limit(1))[0].filename
IndexError: list index out of range

During handling of the above exception, another exception occurred:

Traceback (most recent call last):
  File "D:\qtlab_replacement\qsweepy\qubit_calibrations\readout_pulse.py", line 101, in get_qubit_readout_pulse
    measurement = device.exdir_db.select_measurement(measurement_type='readout_fidelity_scan', metadata=metadata_fidelity_scan, references_that=references)
  File "D:\qtlab_replacement\qsweepy\ponyfiles\exdir_db.py", line 112, in select_measurement
    fi

1 32768
reference: frequency_controls : 19509
good Rabi fits: []
Failed to get readout pulse from fidelity scan, fall back to passthrough
reference: frequency_controls : 19509
reference: channel_calibration : 19516
<class 'IndexError'> list index out of range


Traceback (most recent call last):
  File "D:\qtlab_replacement\qsweepy\qubit_calibrations\readout_pulse.py", line 101, in get_qubit_readout_pulse
    measurement = device.exdir_db.select_measurement(measurement_type='readout_fidelity_scan', metadata=metadata_fidelity_scan, references_that=references)
  File "D:\qtlab_replacement\qsweepy\ponyfiles\exdir_db.py", line 112, in select_measurement
    filename_db = list(measurement_db_list.order_by(lambda d: desc(d.id)).limit(1))[0].filename
IndexError: list index out of range

During handling of the above exception, another exception occurred:

Traceback (most recent call last):
  File "D:\qtlab_replacement\qsweepy\qubit_calibrations\readout_pulse.py", line 101, in get_qubit_readout_pulse
    measurement = device.exdir_db.select_measurement(measurement_type='readout_fidelity_scan', metadata=metadata_fidelity_scan, references_that=references)
  File "D:\qtlab_replacement\qsweepy\ponyfiles\exdir_db.py", line 112, in select_measurement
    fi

1 32768
reference: frequency_controls : 19509
good Rabi fits: []
Failed to get readout pulse from fidelity scan, fall back to passthrough
reference: frequency_controls : 19509
reference: channel_calibration : 19516
<class 'IndexError'> list index out of range
1 32768


KeyboardInterrupt: 

In [13]:
%debug

> c:\programdata\anaconda3\lib\site-packages\usb\backend\libusb0.py(593)ctrl_transfer()
    591                             cast(address, c_char_p),
    592                             length,
--> 593                             timeout
    594                         ))
    595 

ipdb> exit


In [10]:
from qsweepy.qubit_calibrations import Rabi, channel_amplitudes
Rabi.Rabi_rect_adaptive(device, '1', 
            channel_amplitudes = channel_amplitudes.channel_amplitudes(device, iq_ex1_q1=1.0), expected_frequency=20e6)

Requested:  metadata: {'iq_ex1_q1': '1.0'} references: {('channel_calibration', 'iq_ex1_q1'): 19763}
reference: ('channel_calibration', 'iq_ex1_q1') : 19763
Obtained:  metadata: {'iq_ex1_q1': '1.0'} references: {'channel_calibration': 19763}
0 8e-08 1e-09
invoking get_qubit_readout_pulse on line 58
reference: frequency_controls : 19680
reference: channel_calibration : 19691
reference: frequency_controls : 19680
reference: channel_calibration : 19691
Failed to get readout pulse from fidelity scan, fall back to passthrough
reference: frequency_controls : 19680
reference: channel_calibration : 19691


Traceback (most recent call last):
  File "D:\qtlab_replacement\qsweepy\qubit_calibrations\readout_pulse.py", line 101, in get_qubit_readout_pulse
    measurement = device.exdir_db.select_measurement(measurement_type='readout_fidelity_scan', metadata=metadata_fidelity_scan, references_that=references)
  File "D:\qtlab_replacement\qsweepy\ponyfiles\exdir_db.py", line 112, in select_measurement
    filename_db = list(measurement_db_list.order_by(lambda d: desc(d.id)).limit(1))[0].filename
IndexError: list index out of range
Traceback (most recent call last):
  File "D:\qtlab_replacement\qsweepy\qubit_calibrations\readout_pulse.py", line 191, in get_uncalibrated_measurer
    qubit_readout_pulse_, measurer = get_calibrated_measurer(device, [qubit_id], recalibrate=False)
  File "D:\qtlab_replacement\qsweepy\qubit_calibrations\calibrated_readout.py", line 58, in get_calibrated_measurer
    qubit_readout_pulse = get_multi_qubit_readout_pulse(device, qubit_ids, recalibrate=recalibrate)
  File 

reference: passthrough_measurement : 19783
reference: readout_pulse : 19784
reference: modem_calibration : 19726
1 32768
initial_axes_order [(2, 0)]
first_point:  48272 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 200 nop 49600 post_delay 1320 pre_delay 48080 pre_delay_reg 6010
first_point:  48264 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 200 nop 49600 post_delay 1320 pre_delay 48080 pre_delay_reg 6010
first_point:  48256 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 200 nop 49600 post_delay 1320 pre_delay 48080 pre_delay_reg 6010
first_point:  48256 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 200 nop 49600 post_delay 1320 pre_delay 48080 pre_delay_reg 6010
first_point

first_point:  48056 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 600 nop 49600 post_delay 1320 pre_delay 47680 pre_delay_reg 5960
first_point:  48048 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 600 nop 49600 post_delay 1320 pre_delay 47680 pre_delay_reg 5960
first_point:  48040 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 600 nop 49600 post_delay 1320 pre_delay 47680 pre_delay_reg 5960
first_point:  48040 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 600 nop 49600 post_delay 1320 pre_delay 47680 pre_delay_reg 5960
first_point:  48032 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 600 nop 49600 p

first_point:  47840 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 600 nop 49600 post_delay 1320 pre_delay 47680 pre_delay_reg 5960
first_point:  47832 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 600 nop 49600 post_delay 1320 pre_delay 47680 pre_delay_reg 5960
Waiting to join deferred threads:
load time:  0.04097151756286621
pre_trace_time:  0.0
trace 0 time:  0.013993501663208008
trace 1 time:  0.0259857177734375
trace 2 time:  0.038977861404418945
trace 3 time:  0.05296778678894043
load time:  0.03997397422790527
pre_trace_time:  0.0009989738464355469
trace 0 time:  0.013992547988891602
trace 1 time:  0.025984764099121094
trace 2 time:  0.03897690773010254
trace 3 time:  0.05196809768676758
invoking get_qubit_readout_pulse on line 58
reference: frequency_controls : 19680
reference: channel_calibration : 19691
reference: frequen

Traceback (most recent call last):
  File "D:\qtlab_replacement\qsweepy\qubit_calibrations\readout_pulse.py", line 101, in get_qubit_readout_pulse
    measurement = device.exdir_db.select_measurement(measurement_type='readout_fidelity_scan', metadata=metadata_fidelity_scan, references_that=references)
  File "D:\qtlab_replacement\qsweepy\ponyfiles\exdir_db.py", line 112, in select_measurement
    filename_db = list(measurement_db_list.order_by(lambda d: desc(d.id)).limit(1))[0].filename
IndexError: list index out of range
Traceback (most recent call last):
  File "D:\qtlab_replacement\qsweepy\qubit_calibrations\readout_pulse.py", line 191, in get_uncalibrated_measurer
    qubit_readout_pulse_, measurer = get_calibrated_measurer(device, [qubit_id], recalibrate=False)
  File "D:\qtlab_replacement\qsweepy\qubit_calibrations\calibrated_readout.py", line 58, in get_calibrated_measurer
    qubit_readout_pulse = get_multi_qubit_readout_pulse(device, qubit_ids, recalibrate=recalibrate)
  File 

reference: passthrough_measurement : 19783
reference: readout_pulse : 19784
reference: modem_calibration : 19726
1 32768
initial_axes_order [(2, 0)]
first_point:  48224 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 200 nop 49600 post_delay 1320 pre_delay 48080 pre_delay_reg 6010
first_point:  48168 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 200 nop 49600 post_delay 1320 pre_delay 48080 pre_delay_reg 6010
first_point:  48112 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 200 nop 49600 post_delay 1320 pre_delay 48080 pre_delay_reg 6010
first_point:  48056 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 600 nop 49600 post_delay 1320 pre_delay 47680 pre_delay_reg 5960
first_point

first_point:  46056 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 6000 nop 49600 post_delay 1320 pre_delay 42280 pre_delay_reg 5285
first_point:  46000 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 6000 nop 49600 post_delay 1320 pre_delay 42280 pre_delay_reg 5285
first_point:  45944 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 6000 nop 49600 post_delay 1320 pre_delay 42280 pre_delay_reg 5285
first_point:  45888 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 6000 nop 49600 post_delay 1320 pre_delay 42280 pre_delay_reg 5285
first_point:  45832 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 6000 nop 49

first_point:  43888 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 6000 nop 49600 post_delay 1320 pre_delay 42280 pre_delay_reg 5285
first_point:  43832 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 6000 nop 49600 post_delay 1320 pre_delay 42280 pre_delay_reg 5285
Waiting to join deferred threads:
load time:  0.040975332260131836
pre_trace_time:  0.0009989738464355469
trace 0 time:  0.015990257263183594
trace 1 time:  0.028981924057006836
trace 2 time:  0.04197382926940918
trace 3 time:  0.05396628379821777
load time:  0.03897714614868164
pre_trace_time:  0.0009984970092773438
trace 0 time:  0.014990806579589844
trace 1 time:  0.027982711791992188
trace 2 time:  0.04197406768798828
trace 3 time:  0.05496644973754883


ValueError: Failed measuring Rabi frequency for qubit 1 on channel_amplitudes {'iq_ex1_q1': '1.0'}

# Flux pulses for qubit #1 (from minimum to collective state)

In [12]:
freqs_collective = {qubit_id: 5.808e9 for qubit_id in device.get_qubit_list()}
freqs_q1_min = {qubit_id: 5.808e9 if qubit_id != '1' else device.get_qubit_fq('1') for qubit_id in device.get_qubit_list()}
flux_amp = (hardware.mcfq.freqs2volts(freqs_collective)[14]-hardware.mcfq.freqs2volts(freqs_q1_min)[14])

reference: frequency_controls : 15410


In [13]:
zgates = {'z1':{'carrier_name':'coil',
                'amplitude':flux_amp,
                'tail_length':5e-9,
                'target_qubit_id':'1',
                'pre_pause': 50e-9,
                'post_pause':50e-9},
          'z1-ha':{'carrier_name':'coil',
                'amplitude':flux_amp/2.,
                'tail_length':20e-9,
                'target_qubit_id':'1',
                'pre_pause': 50e-9,
                'post_pause':50e-9},
         'empty':{'carrier_name':'coil',
                'amplitude':0.,
                'tail_length':20e-9,
                'target_qubit_id':'1',
                'pre_pause': 50e-9,
                'post_pause':50e-9}}
device.set_zgates_from_dict(zgates)

In [14]:
from qsweepy.qubit_calibrations import zgate

#zgate.zgate_ramsey(device, gate)

In [22]:
from qsweepy.qubit_calibrations import zgate
from qsweepy.fitters import fit_dataset
from qsweepy.qubit_calibrations import Ramsey
import importlib
imp.reload(zgate)
imp.reload(fit_dataset)
imp.reload(Ramsey)
gate = device.get_zgates()['z1']
zgate.zgate_amplitude_ramsey(device, gate, np.linspace(0, 2000e-9, 201), 
                             #np.linspace(-.1, .1, 21), 
                             target_freq_offset=-25e6)

reference: frequency_controls : 15410
reference: channel_calibration : 15490
reference: fidelity_scan : 15561
reference: ('readout_pulse', '1') : 15562
reference: readout_pulse : 15563
reference: delay_calibration : 15517
reference: channel_amplitudes : 15577
reference: gauss_hd_Rabi_amplitude_adaptive : 15601
Exdir_db.select_measurement_by_id: trying to load measurement state by id:  d:\data\2020-04-01\015577-channel_amplitudes-1910-0802-array
reference: channel_amplitudes : 15577
reference: gauss_hd_Rabi_amplitude_adaptive : 15601
Exdir_db.select_measurement_by_id: trying to load measurement state by id:  d:\data\2020-04-01\015577-channel_amplitudes-1910-0802-array
initial_axes_order [(0, 0), (2, 1)]
Requested:  metadata: {'coil': '-0.1'} references: {}
Obtained:  metadata: {'coil': '-0.1'} references: {}
first_point:  0 last_point:  48776 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 49600 nop 49600 post_delay 1648 pre_dela

first_point:  47808 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 600 nop 49600 post_delay 1320 pre_delay 47680 pre_delay_reg 5960
Requested:  metadata: {'coil': '-0.1'} references: {}
Obtained:  metadata: {'coil': '-0.1'} references: {}
first_point:  0 last_point:  48776 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 49600 nop 49600 post_delay 1648 pre_delay 0 pre_delay_reg 0
first_point:  47792 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 600 nop 49600 post_delay 1320 pre_delay 47680 pre_delay_reg 5960
Requested:  metadata: {'coil': '-0.1'} references: {}
Obtained:  metadata: {'coil': '-0.1'} references: {}
first_point:  0 last_point:  48776 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 49600 nop 49600 post_del

first_point:  47648 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 2000 nop 49600 post_delay 1320 pre_delay 46280 pre_delay_reg 5785
Requested:  metadata: {'coil': '-0.1'} references: {}
Obtained:  metadata: {'coil': '-0.1'} references: {}
first_point:  0 last_point:  48776 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 49600 nop 49600 post_delay 1648 pre_delay 0 pre_delay_reg 0
first_point:  47632 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 2000 nop 49600 post_delay 1320 pre_delay 46280 pre_delay_reg 5785
Requested:  metadata: {'coil': '-0.1'} references: {}
Obtained:  metadata: {'coil': '-0.1'} references: {}
first_point:  0 last_point:  48776 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 49600 nop 49600 post_d

first_point:  47488 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 2000 nop 49600 post_delay 1320 pre_delay 46280 pre_delay_reg 5785
Requested:  metadata: {'coil': '-0.1'} references: {}
Obtained:  metadata: {'coil': '-0.1'} references: {}
first_point:  0 last_point:  48776 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 49600 nop 49600 post_delay 1648 pre_delay 0 pre_delay_reg 0
first_point:  47472 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 2000 nop 49600 post_delay 1320 pre_delay 46280 pre_delay_reg 5785
Requested:  metadata: {'coil': '-0.1'} references: {}
Obtained:  metadata: {'coil': '-0.1'} references: {}
first_point:  0 last_point:  48776 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 49600 nop 49600 post_d

first_point:  47328 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 2000 nop 49600 post_delay 1320 pre_delay 46280 pre_delay_reg 5785
Requested:  metadata: {'coil': '-0.1'} references: {}
Obtained:  metadata: {'coil': '-0.1'} references: {}
first_point:  0 last_point:  48776 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 49600 nop 49600 post_delay 1648 pre_delay 0 pre_delay_reg 0
first_point:  47312 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 2000 nop 49600 post_delay 1320 pre_delay 46280 pre_delay_reg 5785
Requested:  metadata: {'coil': '-0.1'} references: {}
Obtained:  metadata: {'coil': '-0.1'} references: {}
first_point:  0 last_point:  48776 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 49600 nop 49600 post_d

...

first_point:  46504 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 2000 nop 49600 post_delay 1320 pre_delay 46280 pre_delay_reg 5785
Requested:  metadata: {'coil': '0.1'} references: {}
Obtained:  metadata: {'coil': '0.1'} references: {}
first_point:  0 last_point:  48776 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 49600 nop 49600 post_delay 1648 pre_delay 0 pre_delay_reg 0
first_point:  46496 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 2000 nop 49600 post_delay 1320 pre_delay 46280 pre_delay_reg 5785
Requested:  metadata: {'coil': '0.1'} references: {}
Obtained:  metadata: {'coil': '0.1'} references: {}
first_point:  0 last_point:  48776 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 49600 nop 49600 post_delay

first_point:  46344 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 2000 nop 49600 post_delay 1320 pre_delay 46280 pre_delay_reg 5785
Requested:  metadata: {'coil': '0.1'} references: {}
Obtained:  metadata: {'coil': '0.1'} references: {}
first_point:  0 last_point:  48776 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 49600 nop 49600 post_delay 1648 pre_delay 0 pre_delay_reg 0
first_point:  46336 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 2000 nop 49600 post_delay 1320 pre_delay 46280 pre_delay_reg 5785
Requested:  metadata: {'coil': '0.1'} references: {}
Obtained:  metadata: {'coil': '0.1'} references: {}
first_point:  0 last_point:  48776 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 49600 nop 49600 post_delay

first_point:  46184 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 6000 nop 49600 post_delay 1320 pre_delay 42280 pre_delay_reg 5285
Requested:  metadata: {'coil': '0.1'} references: {}
Obtained:  metadata: {'coil': '0.1'} references: {}
first_point:  0 last_point:  48776 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 49600 nop 49600 post_delay 1648 pre_delay 0 pre_delay_reg 0
first_point:  46176 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 6000 nop 49600 post_delay 1320 pre_delay 42280 pre_delay_reg 5285
Requested:  metadata: {'coil': '0.1'} references: {}
Obtained:  metadata: {'coil': '0.1'} references: {}
first_point:  0 last_point:  48776 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 49600 nop 49600 post_delay

first_point:  46024 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 6000 nop 49600 post_delay 1320 pre_delay 42280 pre_delay_reg 5285
Requested:  metadata: {'coil': '0.1'} references: {}
Obtained:  metadata: {'coil': '0.1'} references: {}
first_point:  0 last_point:  48776 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 49600 nop 49600 post_delay 1648 pre_delay 0 pre_delay_reg 0
first_point:  46016 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 6000 nop 49600 post_delay 1320 pre_delay 42280 pre_delay_reg 5285
Requested:  metadata: {'coil': '0.1'} references: {}
Obtained:  metadata: {'coil': '0.1'} references: {}
first_point:  0 last_point:  48776 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 49600 nop 49600 post_delay

start: 2020-04-01 16:37:46.768642, started/done/total sweeps: 0/4221/4221, 
Measured data: 
'iq1': parameters: amplitude (),:[-0.1, 0.1] (21 points) with setter
Delay (s),:[0.0, 2e-06] (201 points) with setter
data: [[21652. 26183. 30874. ... 26796. 26835. 26221.]
 [22409. 21773. 22681. ... 27907. 27782. 28158.]
 [25077. 24724. 24172. ... 26261. 26315. 26962.]
 ...
 [17385. 19827. 23476. ... 22927. 22765. 23425.]
 [18874. 25922. 27631. ... 24011. 23013. 22728.]
 [24364. 29837. 19096. ... 21086. 21234. 21530.]]

In [28]:
gate.metadata

{'carrier_name': 'coil',
 'amplitude': '0.0',
 'tail_length': '2e-08',
 'target_qubit_id': '1',
 'pre_pause': '5e-08',
 'post_pause': '5e-08',
 'gate_id': 'empty'}

# Gaussian pulses

In [38]:
from qsweepy.qubit_calibrations import Rabi
from qsweepy.qubit_calibrations import gauss_hd
from qsweepy.qubit_calibrations import channel_amplitudes
#Rabi.Rabi_rect_adaptive(device, '1', channel_amplitudes=channel_amplitudes.channel_amplitudes(device, {'iq_ex1_q1':1.}))
gauss_hd.gauss_hd_Rabi_amplitude_adaptive(device, '1', 4)
gauss_hd.gauss_hd_Rabi_amplitude_adaptive(device, '1', 2)

reference: frequency_controls : 15410
good Rabi fits: []
Requested:  metadata: {'iq_ex1_q1': '1.0'} references: {('channel_calibration', 'iq_ex1_q1'): 15678}
reference: ('channel_calibration', 'iq_ex1_q1') : 15678
Obtained:  metadata: {'iq_ex1_q1': '1.0'} references: {('channel_calibration', 'iq_ex1_q1'): 15678}
reference: frequency_controls : 15410
good Rabi fits: []
0 8e-08 1e-09
reference: frequency_controls : 15410
reference: channel_calibration : 15490
reference: fidelity_scan : 15561
reference: ('readout_pulse', '1') : 15562
reference: readout_pulse : 15563
reference: delay_calibration : 15517
initial_axes_order [(2, 0)]
first_point:  48272 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 200 nop 49600 post_delay 1320 pre_delay 48080 pre_delay_reg 6010
first_point:  48272 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 200 nop 49

first_point:  48240 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 200 nop 49600 post_delay 1320 pre_delay 48080 pre_delay_reg 6010
first_point:  48240 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 200 nop 49600 post_delay 1320 pre_delay 48080 pre_delay_reg 6010
first_point:  48240 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 200 nop 49600 post_delay 1320 pre_delay 48080 pre_delay_reg 6010
first_point:  48240 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 200 nop 49600 post_delay 1320 pre_delay 48080 pre_delay_reg 6010
first_point:  48232 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 200 nop 49600 p

first_point:  47936 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 600 nop 49600 post_delay 1320 pre_delay 47680 pre_delay_reg 5960
first_point:  47928 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 600 nop 49600 post_delay 1320 pre_delay 47680 pre_delay_reg 5960
first_point:  47920 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 600 nop 49600 post_delay 1320 pre_delay 47680 pre_delay_reg 5960
first_point:  47904 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 600 nop 49600 post_delay 1320 pre_delay 47680 pre_delay_reg 5960
first_point:  47896 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 600 nop 49600 p

first_point:  47544 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 2000 nop 49600 post_delay 1320 pre_delay 46280 pre_delay_reg 5785
first_point:  47536 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 2000 nop 49600 post_delay 1320 pre_delay 46280 pre_delay_reg 5785
first_point:  47528 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 2000 nop 49600 post_delay 1320 pre_delay 46280 pre_delay_reg 5785
first_point:  47520 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 2000 nop 49600 post_delay 1320 pre_delay 46280 pre_delay_reg 5785
first_point:  47504 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 2000 nop 49

Traceback (most recent call last):
  File "D:\qtlab_replacement\qsweepy\qubit_calibrations\excitation_pulse.py", line 124, in __init__
    measurement = self.device.exdir_db.select_measurement(measurement_type='qubit_excitation_pulse', metadata=metadata, references_that=references)
  File "D:\qtlab_replacement\qsweepy\ponyfiles\exdir_db.py", line 112, in select_measurement
    filename_db = list(measurement_db_list.order_by(lambda d: desc(d.id)).limit(1))[0].filename
IndexError: list index out of range


...

first_point:  47896 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 600 nop 49600 post_delay 1320 pre_delay 47680 pre_delay_reg 5960
first_point:  47896 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 600 nop 49600 post_delay 1320 pre_delay 47680 pre_delay_reg 5960
first_point:  47896 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 600 nop 49600 post_delay 1320 pre_delay 47680 pre_delay_reg 5960
first_point:  47896 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 600 nop 49600 post_delay 1320 pre_delay 47680 pre_delay_reg 5960
first_point:  47896 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 600 nop 49600 p

first_point:  46744 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 2000 nop 49600 post_delay 1320 pre_delay 46280 pre_delay_reg 5785
first_point:  46744 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 2000 nop 49600 post_delay 1320 pre_delay 46280 pre_delay_reg 5785
first_point:  46744 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 2000 nop 49600 post_delay 1320 pre_delay 46280 pre_delay_reg 5785
first_point:  46744 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 2000 nop 49600 post_delay 1320 pre_delay 46280 pre_delay_reg 5785
first_point:  46744 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 2000 nop 49

first_point:  42136 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 20000 nop 49600 post_delay 1320 pre_delay 28280 pre_delay_reg 3535
first_point:  42136 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 20000 nop 49600 post_delay 1320 pre_delay 28280 pre_delay_reg 3535
first_point:  42136 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 20000 nop 49600 post_delay 1320 pre_delay 28280 pre_delay_reg 3535
first_point:  42136 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 20000 nop 49600 post_delay 1320 pre_delay 28280 pre_delay_reg 3535
first_point:  42136 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 20000 n

first_point:  35992 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 20000 nop 49600 post_delay 1320 pre_delay 28280 pre_delay_reg 3535
first_point:  35992 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 20000 nop 49600 post_delay 1320 pre_delay 28280 pre_delay_reg 3535
Waiting to join deferred threads:
load time:  0.037928104400634766
pre_trace_time:  0.0009982585906982422
trace 0 time:  0.01397252082824707


start: 2020-04-02 02:02:00.101202, started/done/total sweeps: 0/0/0, 
Measured data: 

# Process tomogrpahy for flux pulses with different fronts and lengths

In [15]:
gate = device.get_zgates()['z1']
gate.metadata

{'carrier_name': 'coil',
 'amplitude': '0.3410960386444185',
 'tail_length': '5e-09',
 'target_qubit_id': '1',
 'pre_pause': '5e-08',
 'post_pause': '5e-08',
 'gate_id': 'z1'}

In [19]:
from qsweepy.qubit_calibrations import state_tomography, excitation_pulse, channel_amplitudes
imp.reload(state_tomography)
gate = device.get_zgates()['z1']
process_tomography_inst = state_tomography.ProcessTomography(device, ['1'], pause_length=50e-9)
process_tomography_inst.set_prepare_seq(
    excitation_pulse.get_excitation_pulse(device, qubit_id='1', rotation_angle=np.pi/2.).get_pulse_sequence(0.0))

class PulseSettings:
    def __init__(self, process_tomography_inst, zgate):
        self.length = 0
        self.tail_length = float(zgate.metadata['tail_length'])
        self.pre_pause = float(zgate.metadata['pre_pause'])
        self.post_pause = float(zgate.metadata['post_pause'])
        self.process_tomography_inst = process_tomography_inst
        self.amplitude = float(zgate.metadata['amplitude'])
        self.channel_name = zgate.metadata['carrier_name']
        self.channel_amplitudes_ = channel_amplitudes.channel_amplitudes(device, **{self.channel_name: self.amplitude})
        self.output = 1
    def set_length(self, length):
        self.length = length
        self.update_pulse()
        self.process_tomography_inst.recalibrate_readout()
    def set_pre_pause(self, pre_pause):
        self.pre_pause = pre_pause
        self.update_pulse()
    def set_post_pause(self, post_pause):
        self.post_pause = post_pause
        self.update_pulse()
    def set_tail_length(self, tail_length):
        self.tail_length = tail_length
        self.update_pulse()
    def set_amplitude(self, amplitude):
        self.amplitude = amplitude
        self.channel_amplitudes_ = channel_amplitudes.channel_amplitudes(device, **{self.channel_name: self.amplitude})
        self.update_pulse()
    def set_output(self, output):
        self.output = output
        self.update_pulse()
        
    def update_pulse(self):
        if self.output > 0:
            pulse_seq = [device.pg.pmulti(self.pre_pause)]+\
            excitation_pulse.get_rect_cos_pulse_sequence(device = device,
                                                         channel_amplitudes = self.channel_amplitudes_ ,
                                                         tail_length = self.tail_length,
                                                         length = self.length,
                                                         phase = 0.0)+\
                                                     [device.pg.pmulti(self.post_pause)]
        else:
            pulse_seq = [device.pg.pmulti(self.pre_pause+self.post_pause)]
        self.process_tomography_inst.set_prepare_seq(pulse_seq)
        
        #self.process_tomography_inst.set_prepare_seq([device.pg.pmulti(0)])

pulse_settings_inst = PulseSettings(process_tomography_inst, zgate=gate)
pulse_lengths = np.linspace(0e-9, 200e-9, 201)
pulse_outputs = [0, 1]
        
references = {'gate': gate.id}
references.update(process_tomography_inst.references)
metadata = process_tomography_inst.metadata

tomography = sweeper.sweep(process_tomography_inst, 
                           (pulse_lengths, pulse_settings_inst.set_length, 'Pulse length', 's'),
                           (pulse_outputs, pulse_settings_inst.set_output, 'Pulse enabled', ''),
                           measurement_type='process_tomography_zgate', references=references, 
                           metadata=metadata)

reference: frequency_controls : 15410
reference: channel_calibration : 15490
reference: fidelity_scan : 16866
reference: ('readout_pulse', '1') : 16867
reference: readout_pulse : 16868
reference: delay_calibration : 15517
reference: channel_amplitudes : 15679
reference: gauss_hd_Rabi_amplitude_adaptive : 15701
Exdir_db.select_measurement_by_id: trying to load measurement state by id:  d:\data\2020-04-02\015679-channel_amplitudes-1910-0802-array
reference: ('excitation_pulse', '1') : 15702
reference: readout_pulse : 16868
reference: channel_amplitudes : 15679
reference: gauss_hd_Rabi_amplitude_adaptive : 15692
Exdir_db.select_measurement_by_id: trying to load measurement state by id:  d:\data\2020-04-02\015679-channel_amplitudes-1910-0802-array
reference: channel_amplitudes : 15679
reference: gauss_hd_Rabi_amplitude_adaptive : 15692
Exdir_db.select_measurement_by_id: trying to load measurement state by id:  d:\data\2020-04-02\015679-channel_amplitudes-1910-0802-array
reference: channel_

Traceback (most recent call last):
  File "D:\qtlab_replacement\qsweepy\qubit_calibrations\calibrated_readout.py", line 68, in get_calibrated_measurer
    raise ValueError('Forcing recalibration')
ValueError: Forcing recalibration


reference: channel_amplitudes : 15679
reference: gauss_hd_Rabi_amplitude_adaptive : 15701
Exdir_db.select_measurement_by_id: trying to load measurement state by id:  d:\data\2020-04-02\015679-channel_amplitudes-1910-0802-array
first_point:  0 last_point:  48776 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 49600 nop 49600 post_delay 1648 pre_delay 0 pre_delay_reg 0
first_point:  48184 last_point:  48280 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 200 nop 49600 post_delay 1320 pre_delay 48080 pre_delay_reg 6010


C:\ProgramData\Anaconda3\lib\site-packages\sklearn\model_selection\_split.py:1978: FutureWarning:

The default value of cv will change from 3 to 5 in version 0.22. Specify it explicitly to silence this warning.



load time:  0.37578725814819336
pre_trace_time:  0.0009965896606445312
trace 0 time:  0.01647019386291504
trace 1 time:  0.030941486358642578
trace 2 time:  0.044914960861206055
trace 3 time:  0.05888819694519043
trace 4 time:  0.0728611946105957
trace 5 time:  0.08683419227600098
trace 6 time:  0.10080742835998535
trace 7 time:  0.11478137969970703
trace 8 time:  0.13025403022766113
trace 9 time:  0.14821767807006836
trace 10 time:  0.17566776275634766
trace 11 time:  0.18914079666137695


...

D:\qtlab_replacement\qsweepy\instrument_drivers\HDAWG_1808_new.py:607: ComplexWarning:

Casting complex values to real discards the imaginary part

C:\ProgramData\Anaconda3\lib\site-packages\numpy\core\numeric.py:538: ComplexWarning:

Casting complex values to real discards the imaginary part



first_point:  0 last_point:  48776 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 49600 nop 49600 post_delay 1648 pre_delay 0 pre_delay_reg 0
first_point:  47824 last_point:  47920 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 200 nop 49600 post_delay 1680 pre_delay 47720 pre_delay_reg 5965
first_point:  47824 last_point:  47920 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 200 nop 49600 post_delay 1680 pre_delay 47720 pre_delay_reg 5965
first_point:  47824 last_point:  47920 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 200 nop 49600 post_delay 1680 pre_delay 47720 pre_delay_reg 5965
first_point:  47824 last_point:  47920 waveformI length (49600,) waveformQ length (49600,) markerI length 49600 markerQ length 49600 wave_length 200 nop 49600 post_delay

load time:  0.12027096748352051
pre_trace_time:  0.0005004405975341797
trace 0 time:  0.047908782958984375
trace 1 time:  0.08833169937133789
trace 2 time:  0.12775659561157227
trace 3 time:  0.16867899894714355


C:\ProgramData\Anaconda3\lib\site-packages\numpy\core\memmap.py:331: FutureWarning:

Using a non-tuple sequence for multidimensional indexing is deprecated; use `arr[tuple(seq)]` instead of `arr[seq]`. In the future this will be interpreted as an array index, `arr[np.array(seq)]`, which will result either in an error or a different result.



trace 4 time:  0.20960140228271484


# Saving quantum process tomography for qubit tuned into array

In [6]:
import pandas
tomography = exdir_db_inst.select_measurement_by_id(18652)
projections = [k+j for k in tomography.metadata.keys() for j in tomography.metadata.keys()]
reference_meas = pandas.DataFrame(np.reshape(tomography.datasets['measurement'].data[:,0,:,:,0], (201, 36)), columns = projections)
data = pandas.DataFrame(np.reshape(tomography.datasets['measurement'].data[:,1,:,:,0], (201, 36)), columns = projections)
data[tomography.datasets['measurement'].parameters[0].name] = tomography.datasets['measurement'].parameters[0].values
reference_meas.to_csv('reference_tomography_array.tsv', sep='\t')
data.to_csv('data_tomography_array.tsv', sep='\t')

Exdir_db.select_measurement_by_id: trying to load measurement state by id:  d:\data\2020-04-10\018652-process_tomography_zgate-1910-0802-array


# Zgate FPI plotting

In [26]:
def P0_init_load(index):
    print(index)
    P=exdir_db_inst.select_measurement_by_id(index)
    Pin=P.metadata
    P0=[]
    P0.append(float(Pin['frb']))
    P0.append(float(Pin['Cc']))
    P0.append(float(Pin['EJ1']))
    P0.append(float(Pin['EJ2']))
    P0.append(float(Pin['EC']))
    P0.append(float(Pin['phi0']))
    P0.append(float(Pin['L']))
    print(P0)
    return P0
qubit_id='1'
meas = exdir_db_inst.select_measurement(measurement_type="Adaptive_two_tone_spectroscopy", 
                            metadata={'qubit_id':qubit_id, 'probe_power':-53.0})
    
    
P0=P0_init_load(meas.references['P0_podgon'])

x = meas.datasets['S-parameter'].parameters[0].values[:]
y = meas.datasets['S-parameter'].parameters[1].values[:]
z = meas.datasets['S-parameter'].data[:,:,0]
z = np.abs(z)
    
P1=P0_init_load(meas.references['P0_podgon'])
P1[5]=P1[5]-0.02
two_tone_adaptive_plot(x,y,z,P0,None,None)


8716
Exdir_db.select_measurement_by_id: trying to load measurement state by id:  d:\data\2020-02-18\008716-Nondiag_Two_tone_parameters-1910-0802-array
[5375853660.0, 0.00517054335, 26125370500.0, 9551854470.0, 145083556.0, 0.12891732294729577, 0.661229495]
8716
Exdir_db.select_measurement_by_id: trying to load measurement state by id:  d:\data\2020-02-18\008716-Nondiag_Two_tone_parameters-1910-0802-array
[5375853660.0, 0.00517054335, 26125370500.0, 9551854470.0, 145083556.0, 0.12891732294729577, 0.661229495]


In [27]:
def fq_coil(p,x):
    frb, Cc, EJ1, EJ2, EC, phi0 = p[:6]
    L = p[-1]
    return fq_1R(x, frb, Cc, EJ1, EJ2, EC, phi0, L)/1e9
def fr_coil(p,x):
    frb, Cc, EJ1, EJ2, EC, phi0 = p[:6]
    L = p[6:]
    return fR_1Q(x, frb, Cc, EJ1, EJ2, EC, phi0, L)/1e9

def fR_1Q(x, frb, Cc, EJ1, EJ2, EC, phi0,L):
    f_qubit=fQ(x, EJ1, EJ2, EC, phi0, L)
    f_QR=(f_qubit+frb)*0.5-(((f_qubit-frb)*0.5)**2+Cc**2*f_qubit*frb)**0.5*np.sign(-frb+f_qubit)
    return f_QR

def fQ(x, EJ1, EJ2, EC, phi0, L):
        #f_qubit=fqb(x, EJ1, EJ2, EC, phi0, L)
    f_qubit=(8*EC)**0.5*((EJ1-EJ2)**2*np.sin(np.pi*x*L+phi0*np.pi)**2+\
                                                    (EJ1+EJ2)**2*np.cos(np.pi*x*L+phi0*np.pi)**2)**0.25
    return f_qubit
    
def fq_1R(x, frb, Cc, EJ1, EJ2, EC, phi0,L):
    f_qubit=fQ(x, EJ1, EJ2, EC, phi0, L)
    f_QR=(f_qubit+frb)*0.5-(((f_qubit-frb)*0.5)**2+Cc**2*f_qubit*frb)**0.5*np.sign(frb-f_qubit)
    return f_QR

def fq_1R(x, frb, Cc, EJ1, EJ2, EC, phi0,L):
    f_qubit=fQ(x, EJ1, EJ2, EC, phi0, L)
    f_QR=(f_qubit+frb)*0.5-(((f_qubit-frb)*0.5)**2+Cc**2*f_qubit*frb)**0.5*np.sign(frb-f_qubit)
    return f_QR
    
def fQ_2R_coil(p,x):
    frb, Cc, EJ1, EJ2, EC, phi0 = p[:6]
    L = p[6]
    fr_com=p[7]
    Ccom=p[8]
    if frb<fr_com:
        fq1R=fq_1R(x,frb, Cc, EJ1, EJ2, EC, phi0,L)
        fq2R=(fq1R+fr_com)*0.5-(((fq1R-fr_com)*0.5)**2+Ccom**2*fq1R*fr_com)**0.5*np.sign(fr_com-fq1R)
    else:
        fq1R=fq_1R(x,fr_com, Ccom, EJ1, EJ2, EC, phi0,L)
        fq2R=(fq1R+frb)*0.5-(((fq1R-frb)*0.5)**2+Cc**2*fq1R*frb)**0.5*np.sign(frb-fq1R)
        
    return fq2R/1e9

In [28]:
def two_tone_adaptive_plot(x,y,z,fit_params,fit=None,axes=None, offset=0):
    if not axes:
        plt.figure()
        axes = plt.gca()
    fr_diag=fq_coil(fit_params,x)
    step=np.abs(x[1]-x[0])/2
    vmin=np.min(z)
    vmax=np.max(z)
    for _id in range(len(x)):
        x_plot1 = (x[_id]-step)-offset
        x_plot2 = (x[_id]+step)-offset
        
        im = axes.pcolormesh((y/1e9+fr_diag[_id]),[x_plot1, x_plot2],
                        np.asarray([z[_id,:],z[_id,:]]).reshape(2,len(y)), cmap='RdBu_r', vmin=vmin, vmax=vmax)
    if fit is not None:
        axes.plot(x,fit,'go')
    return im

In [29]:
fig, axes = plt.subplots(2,2, figsize=(11,9), sharey=True)
freqs =np.linspace(0, 500, 101)
meas = exdir_db_inst.select_measurement(measurement_type='Ramsey_amplitude_scan')
fit = exdir_db_inst.select_measurement(measurement_type='fit_dataset_1d', references_that={'fit_source':meas.id})
times = meas.datasets['iq1'].parameters[1].values
amplitudes = meas.datasets['iq1'].parameters[0].values
data = meas.datasets['iq1'].data
spectrum = np.fft.fft(np.fft.fftshift(data, axes=1), axis=1)
im_data = axes[0,0].pcolormesh(times*1e9, amplitudes, data, cmap='RdBu_r')
im_fit = axes[0,1].pcolormesh(fit.datasets['iq1'].parameters[1].values*1e9, 
                             amplitudes, np.real(fit.datasets['iq1'].data), 
                            vmin=np.min(data), vmax=np.max(data), cmap='RdBu_r')
im_spectrum = axes[1,0].pcolormesh(freqs, amplitudes,np.log10(np.abs(spectrum)[:, :101]), cmap='RdBu_r')
f_fit = fit.datasets['f'].data/1e6
axes[1,0].scatter(f_fit, amplitudes, color='black', marker='.', s=1)

im_two_tone = two_tone_adaptive_plot(x,y,z,P0,axes=axes[1,1], offset=0.55)
p1 = amplitudes>-0.113
p2 = np.logical_and(amplitudes<-0.113, amplitudes>-0.234)
p3 = np.logical_and(amplitudes<-0.234, amplitudes>-0.353)
p4 = amplitudes<-0.353
axes[1,1].scatter(-(f_fit[p1]-300)/1e3+device.get_qubit_fq('1')/1e9, amplitudes[p1], marker='o', s=3, color='C1')
axes[1,1].scatter((f_fit[p2]+300)/1e3+device.get_qubit_fq('1')/1e9, amplitudes[p2], marker='o', s=3, color='C2')
axes[1,1].scatter(-(f_fit[p3]-1300)/1e3+device.get_qubit_fq('1')/1e9, amplitudes[p3], marker='o', s=3, color='C3')
axes[1,1].scatter((f_fit[p4]+1300)/1e3+device.get_qubit_fq('1')/1e9, amplitudes[p4], marker='o', s=3, color='C4')
#axes[3].legend()
#plt.pcolormesh(np.real(exdir_db_inst.select_measurement(
#    measurement_type='fit_dataset_1d').datasets['iq1'].data), vmax=32000, vmin=8000)
plt.colorbar(im_data, ax=axes[0,:])
plt.colorbar(im_spectrum, ax=axes[1,0])
plt.colorbar(im_two_tone, ax=axes[1,1])
axes[0,0].set_xlabel('Время, мкс')
axes[0,1].set_xlabel('Время, мкс')
axes[1,0].set_xlabel('Частота, МГц')
axes[1,1].set_xlabel('Частота, ГГц')
axes[0,0].set_ylabel('Амплитуда импульса, В')
axes[1,0].set_ylabel('Амплитуда импульса, В')
axes[0,0].set_ylim(np.min(amplitudes), np.max(amplitudes))
axes[1,1].set_xlim(4.3, 6.0)
plt.savefig('zgate-results.pdf')
plt.savefig('zgate-results.png')

reference: fit_source : 14850
reference: frequency_controls : 13617
reference: frequency_controls : 13617
reference: frequency_controls : 13617
reference: frequency_controls : 13617


# Reset qubit frequency configurations & rescan resonators

# Time-domain settings

In [6]:
two_qubit_gates = {}
device.set_two_qubit_gates_from_dict(two_qubit_gates)

In [45]:
reload(qubit_device)
reload(exdir_db)
reload(database)
reload(sweep_extras)

# setting pony 
db = database.MyDatabase()
sweeper = sweep_extras.Sweeper(db, sample_name=sample_name)
exdir_db_inst = exdir_db.Exdir_db(db=db, sample_name=sample_name)

qubits = {}
for qubit_id in [ '1', '2', '3', '4', '5', '6', '7', '8', '9', 
                 '11','12','13','14','15','16','18','19','20',
                 '21','22','23','24','25']:
        m = exdir_db_inst.select_measurement(measurement_type='Full_two_tone_fit_Recool',
                                                        metadata={'qubit_id': qubit_id, })
        m2 = exdir_db_inst.select_measurement(measurement_type='resonator_frequency',
                                                        metadata={'qubit_id': qubit_id, })
        fqb = 5.2e9
        frb = float(m.metadata['frb'])
        Cc = float(m.metadata['Cc'])
        
        fr = float(m2.metadata['fr'])

        f_QR = (fqb + frb) * 0.5 - (((fqb - frb) * 0.5) ** 2 + Cc ** 2 * fqb * frb) ** 0.5 * np.sign( -frb + fqb)
        
        qubits[qubit_id] = {'r':{'Fr': fr, # qubit readout frequency
                                 'P':-50, # 
                                 'iq_devices':{'iq_ro_q'+qubit_id: 'iq_ro'}}, # channel name : device name
                            'q': {'iq_devices':{'iq_ex1_q'+qubit_id: 'iq_ex1'},
                                  'iq_devices_transitions':{'iq_ex1_q'+qubit_id: '01'},
                                  'F': {'F01_min': 5.2e9}},                     
                            'main_iq_device': 'iq_ex1_q'+qubit_id}


device = qubit_device.qubit_device(exdir_db_inst, sweeper, controls=hardware.controls)
for qubit_id in qubits.keys():
    device.set_frequency_controls(qubit_id=qubit_id, controls=['fq'+qubit_id])
device.set_qubits_from_dict(qubits)



reference: frequency_controls : 15410
 <class 'AssertionError'>
{'frequency_controls': 15410}
reference: frequency_controls : 15410
 <class 'AssertionError'>
reference: frequency_controls : 19055
 <class 'AssertionError'>
{'frequency_controls': 19055}
reference: frequency_controls : 19055
 <class 'AssertionError'>
reference: frequency_controls : 19057
 <class 'AssertionError'>
{'frequency_controls': 19057}
reference: frequency_controls : 19057
 <class 'AssertionError'>
reference: frequency_controls : 19059
 <class 'AssertionError'>
{'frequency_controls': 19059}
reference: frequency_controls : 19059
 <class 'AssertionError'>
reference: frequency_controls : 19061
 <class 'AssertionError'>
{'frequency_controls': 19061}
reference: frequency_controls : 19061
 <class 'AssertionError'>
reference: frequency_controls : 19063
 <class 'AssertionError'>
{'frequency_controls': 19063}
reference: frequency_controls : 19063
 <class 'AssertionError'>
reference: frequency_controls : 19065
 <class 'Asser

In [11]:
sample_globals={
            'readout_passthrough_points':21,
            'readout_passthrough_amplitude':1.0,
    'readout_length': 0.3e-6,
    'readout_background_nums': 10000,
    'Rabi_rect_length': 400e-9,
    'Rabi_rect_step': 2e-9,
    'Ramsey_length': 10e-6,
    'Ramsey_step': 100e-9,
    'adaptive_Rabi_min_step':1e-9,
    'adaptive_Rabi_scan_points': 80,
    'adaptive_Rabi_range':10,
    'adaptive_Rabi_max_scan_length':20e-6,
    'adaptive_Ramsey_max_scan_length':100e-6,
    'adaptive_Ramsey_points_per_oscillation':10,
    'frequency_rounding':5e3,
    'amplitude_default':1.0,
    'cross_Ramsey_initial_delay':0e-9, ## fix the fitter!!
    'max_parasitic_Rabi_ratio': 0.1, ## maximum Ω_R/Δ for non-target qubits that is 
                ## used to choose the excitation amplitude for the target qubit
    'max_Rabi_freq': 50e9, ## maximum Rabi frequency for target qubit
    'pulse_length_alignment': 32e-9,
    'sigmas_in_gauss': 4,
    'adaptive_Rabi_amplitude_scan_points': 20,
    'adaptive_Rabi_amplitude_range':2,
    'delay_calibration_sequence_length': 10000,
    'uncalibrated_readout_nums': 200000,
    'calibrated_readout_nums': 50000,
    'delay_calibration_nums': 200,
    'delay_calibration_nop': 32768,
    'readout_adc_points': 512,
    'process_phase_scan_points': 50,
    'two_qubit_pulse_post_pause': 0e-9,
    'parametric_frequency_shift_calibration_frequency_offset': 5e6,
    'single_tone_spectrum_span': 20e6,
    'single_tone_spectrum_power': -50,
    'single_tone_spectrum_nop': 201,
    'single_tone_spectrum_bandwidth': 20,
    'single_tone_spectrum_fit_type': 'resonator_tools_notch_port',
    'two_tone_spectrum_span':300e6,
    'two_tone_spectrum_excite_power':18,
    'two_tone_spectrum_readout_power':-50,
    'two_tone_spectrum_nop': 301,
    'two_tone_spectrum_bandwidth':10,
    'readout_calibration_ignore_other_qubits':True,
    'gauss_hd_calibration_ignore_other_qubits':True
}

reload(exdir_db)
reload(database)
reload(sweep_extras)
db = database.MyDatabase()
sweeper = sweep_extras.Sweeper(db, sample_name=sample_name)
exdir_db_inst = exdir_db.Exdir_db(db=db, sample_name=sample_name)
device = qubit_device.qubit_device(exdir_db_inst, sweeper)
device.set_sample_globals(sample_globals)

sample_name

'1910-0802-array'

# Qubit frequency setter

In [28]:
db = database.MyDatabase()

sweeper = sweep_extras.Sweeper(db, sample_name=sample_name)
exdir_db_inst = exdir_db.Exdir_db(db=db, sample_name=sample_name)

## Inductance matrix load

In [7]:
source=exdir_db_inst.select_measurement(measurement_type='Ind_mat_REC23')
Qubit_number=source.datasets['L_mat'].parameters[0].values 
Coil_number=source.datasets['L_mat'].parameters[1].values
L_23=source.datasets['L_mat'].data

import pandas as pd
L_full_REC23 = pd.DataFrame(np.round(L_23, decimals=4), 
                            columns=[coil_id for coil_id in Coil_number], 
                            index=[str(qubit_id) for qubit_id in Qubit_number])
#L_full_REC23

## Functions for qubit + 2 resonators

In [12]:
# helper functions for freqs2volts
def fr_coil(p, x):
    frb, Cc, EJ1, EJ2, EC, phi0 = p[:6]
    L = p[6:]
    return fR_1Q(x, frb, Cc, EJ1, EJ2, EC, phi0, L) / 1e9

def fR_1Q(x, frb, Cc, EJ1, EJ2, EC, phi0, L):
    f_qubit = fQ(x, EJ1, EJ2, EC, phi0, L)
    f_QR = (f_qubit + frb) * 0.5 - (((f_qubit - frb) * 0.5) ** 2 + Cc ** 2 * f_qubit * frb) ** 0.5 * np.sign(
        -frb + f_qubit)
    return f_QR

def fQ(x, EJ1, EJ2, EC, phi0, L):
    # f_qubit=fqb(x, EJ1, EJ2, EC, phi0, L)
    f_qubit = (8 * EC) ** 0.5 * ((EJ1 - EJ2) ** 2 * np.sin(np.pi * x * L + phi0 * np.pi) ** 2 +
                                 (EJ1 + EJ2) ** 2 * np.cos(np.pi * x * L + phi0 * np.pi) ** 2) ** 0.25
    return f_qubit

def fq_1R(x, frb, Cc, EJ1, EJ2, EC, phi0, L):
    f_qubit = fQ(x, EJ1, EJ2, EC, phi0, L)
    f_QR = (f_qubit + frb) * 0.5 - (((f_qubit - frb) * 0.5) ** 2 + Cc ** 2 * f_qubit * frb) ** 0.5 * np.sign(
        frb - f_qubit)
    return f_QR

def fQ_2R_coil(p, x):
    frb, Cc, EJ1, EJ2, EC, phi0 = p[:6]
    L = p[6]
    fr_com = p[7]
    Ccom = p[8]
    if frb < fr_com:
        fq1R = fq_1R(x, frb, Cc, EJ1, EJ2, EC, phi0, L)
        fq2R = (fq1R + fr_com) * 0.5 - (((fq1R - fr_com) * 0.5) ** 2 + Ccom ** 2 * fq1R * fr_com) ** 0.5 * np.sign(
            fr_com - fq1R)
    else:
        fq1R = fq_1R(x, fr_com, Ccom, EJ1, EJ2, EC, phi0, L)
        fq2R = (fq1R + frb) * 0.5 - (((fq1R - frb) * 0.5) ** 2 + Cc ** 2 * fq1R * frb) ** 0.5 * np.sign(frb - fq1R)

    return fq2R / 1e9


## Find voltages for qubits frequency

In [13]:
import scipy.optimize
def volt_matrix_freq(freqs, all_qubits=False,Podgon=True):
    if all_qubits==False:
            all_qubits=['1','2','3','4','5','6','7','8','9','11','12','13','14','15','16','18','19','20','21','22','23','24','25']
    if Podgon==True:
        linear_fit=exdir_db_inst.select_measurement(measurement_type='Podgon_param',)
        b=np.asarray(linear_fit.datasets['K'].parameters[1].values) 
        k=np.asarray(linear_fit.datasets['K'].data)
    else:
        b=np.zeros(23)
        k=np.ones(23)
    Q_real=freqs
    Q_theory=(Q_real-b)/k
    Q_freqs=Q_theory
    phi_vector = np.zeros(len(L_full_REC23.index))
    for _id, qubit_id in enumerate(all_qubits):
        target_freq=Q_freqs[_id]
         
        source=exdir_db_inst.select_measurement(measurement_type='Full_two_tone_fit_Recool', 
                metadata={'qubit_id':qubit_id, })
        p0=[float(source.metadata['frb']),float(source.metadata['Cc']),\
            float(source.metadata['EJ1']),float(source.metadata['EJ2']),\
            float(source.metadata['EC']),float(source.metadata['phi0']),float(source.metadata['L']),\
            float(source.metadata['fr_com']),float(source.metadata['Ccom']),] 
        solutions = []
        for x0 in np.linspace(-0.5, 0.5, 51)/float(source.metadata['L']):

            v = scipy.optimize.root(lambda x: fQ_2R_coil(p0, (x))-target_freq, x0)
            solutions.append(v.x*float(source.metadata['L']))#/(np.pi)
        phi_vector[_id] = solutions[np.argmin(np.abs(solutions))]
    
    voltage_vector = np.linalg.solve(L_full_REC23, phi_vector)
    return voltage_vector

## Voltage set and get

In [14]:
def set_coil_voltage(voltage, qubit_id):
    if qubit_id == '1':
        hardware.awg.set_offset(voltage, channel=0)
        hardware.awg.set_output(1,channel=0)
    else:
        hardware.dac.set_voltage(voltage, channel=Qfrequency[qubit_id]['nndac_coil_id'])

def get_coil_voltage(qubit_id):
    if qubit_id == '1':
        return hardware.awg.get_offset(channel=0)
    else:
        return hardware.dac.get_voltage(Qfrequency[qubit_id]['nndac_coil_id'])

In [15]:
volt_matrix_freq([5.331e9]*23)

array([0.05803421, 0.16065948, 0.13821274, 0.16777909, 0.15788028,
       0.13709103, 0.16469341, 0.15656208, 0.13265065, 0.15195839,
       0.12935858, 0.17391847, 0.14875276, 0.17063002, 0.19723435,
       0.17320897, 0.19352622, 0.14620662, 0.1716328 , 0.1868471 ,
       0.14230498, 0.16803985, 0.18252433])

In [18]:
len(Qfrequency)

23

## Qubit frequency

In [17]:
Qfrequency = {
                '1': {'Fq':5.331e9,
                     'nndac_coil_id':False,},    
                '2': {'Fq':5.331e9,
                     'nndac_coil_id':23,},
                '3': {'Fq':5.331e9,
                     'nndac_coil_id':7,},
                '4': {'Fq':5.331e9,                     
                     'nndac_coil_id':13,},
                '5': {'Fq':5.331e9,                     
                     'nndac_coil_id':21,},
                '6': {'Fq':5.331e9,                     
                     'nndac_coil_id':5,},
                '7': {'Fq':5.331e9,                     
                     'nndac_coil_id':12,},
                '8': {'Fq':5.331e9,                     
                     'nndac_coil_id':19,},
                '9': {'Fq':5.331e9,                     
                     'nndac_coil_id':3,},
                '11': {'Fq':5.331e9,                     
                     'nndac_coil_id':17,},
                '12': {'Fq':5.331e9,                     
                     'nndac_coil_id':1,},
                '13': {'Fq':5.331e9,                     
                     'nndac_coil_id':8,},
                '14': {'Fq':5.331e9,                     
                     'nndac_coil_id':15,},
                '15': {'Fq':5.331e9,                     
                     'nndac_coil_id':22,},
                '16': {'Fq':5.331e9,                     
                     'nndac_coil_id':6,},
                '18': {'Fq':5.331e9,                     
                     'nndac_coil_id':20,},
                '19': {'Fq':5.331e9,                     
                     'nndac_coil_id':4,},
                '20': {'Fq':5.331e9,                     
                     'nndac_coil_id':11,},
                '21': {'Fq':5.331e9,                     
                     'nndac_coil_id':18,},
                '22': {'Fq':5.331e9,                     
                     'nndac_coil_id':2,},
                '23': {'Fq':5.331e9,                     
                     'nndac_coil_id':9,},    
                '24': {'Fq':5.331e9,                     
                     'nndac_coil_id':16,},
                '25': {'Fq':5.331e9,                     
                     'nndac_coil_id':0,},}


In [42]:
from copy import copy

def set_qubit_frequency(Fq, qubit_id):
    all_qubits=['1','2','3','4','5','6','7','8','9','11','12','13','14','15','16','18','19','20','21','22','23','24','25']
    
    #copy frequency values
    Old_Freqs=[]
    for q_id in Qfrequency.keys():
        Old_Freqs.append(Qfrequency[q_id]['Fq']/1e9)
    
    #write new frequency
    New_Freqs=Old_Freqs.copy()
    New_Freqs[all_qubits.index(qubit_id)]=Fq
    
    #rewrite new frequences
    for q_id in Qfrequency.keys():
        Qfrequency[q_id]['Fq']=New_Freqs[all_qubits.index(q_id)]*1e9
    
    #find voltages
    Voltages=volt_matrix_freq(freqs=np.asarray(New_Freqs))
    
    #set voltages
    for _id,res_id in enumerate(all_qubits):
        set_coil_voltage(voltage=Voltages[_id], qubit_id=res_id)
    
    return New_Freqs
    
    

In [45]:
set_qubit_frequency(Fq=5.5, qubit_id='2')

[5.331,
 5.5,
 5.331,
 5.331,
 5.331,
 5.331,
 5.331,
 5.331,
 5.331,
 5.331,
 5.331,
 5.331,
 5.331,
 5.331,
 5.331,
 5.331,
 5.331,
 5.331,
 5.331,
 5.331,
 5.331,
 5.331,
 5.331]

In [ ]:
pulse_amp = 